# Extract Conversations from French Classic Books

This notebook extracts character dialogues from `Volko76/french-classic-books` and formats them as conversation pairs for LLM finetuning.

**Pipeline:**
1. Re-download PDFs with preserved paragraph structure (line breaks)
2. Extract dialogues using French dialogue markers (`«»`, `–`, `—`, `―`)
3. Build multi-turn conversations with user/assistant roles
4. Add contextual system prompts
5. Push to HuggingFace Hub

In [1]:
%pip install requests PyMuPDF beautifulsoup4 datasets huggingface_hub tqdm

In [15]:
import os
import re
import json
import requests
import fitz  # PyMuPDF
from urllib.parse import urlparse, unquote, urljoin
from bs4 import BeautifulSoup
from tqdm import tqdm
from datasets import Dataset
from huggingface_hub import login

# ============================================================================
# CONFIGURATION
# ============================================================================

# Dialogue markers in French literature
DIALOGUE_MARKERS = [
    '–',    # en dash (U+2013) - most common
    '—',    # em dash (U+2014)
    '―',    # horizontal bar (U+2015) - quotation dash
    '-',    # hyphen (sometimes used)
]

# Opening/closing guillemets
GUILLEMET_OPEN = '«'
GUILLEMET_CLOSE = '»'

# Speech attribution patterns (to clean from dialogues)
SPEECH_ATTRIBUTION_PATTERN = re.compile(
    r',?\s*'
    r'(dit|répondit|demanda|s\'écria|murmura|ajouta|reprit|continua|'
    r'répliqua|interrompit|chuchota|souffla|gémit|hurla|cria|soupira|'
    r'grommela|bégaya|balbutia|articula|prononça|déclara|affirma|'
    r'interrogea|questionna|implora|supplia|ordonna|commanda|suggéra|'
    r'proposa|observa|remarqua|nota|constata|admit|avoua|confessa|'
    r'expliqua|précisa|annonça|fit|fis|firent)'
    r'[-\s]*(il|elle|je|tu|nous|vous|ils|elles|on|'
    r'le\s+\w+|la\s+\w+|l\'\w+|un\s+\w+|une\s+\w+|'
    r'\w+)?'
    r'[.,;:]?\s*$',
    re.IGNORECASE
)

# Minimum characters for a valid dialogue turn
MIN_DIALOGUE_LENGTH = 15

# Maximum turns per conversation (for multi-turn)
MAX_TURNS_PER_CONVERSATION = 8

print("✅ Configuration loaded!")

✅ Configuration loaded!


## Step 1: PDF Processing Functions (with preserved line breaks)

In [16]:
# ============================================================================
# PDF DOWNLOAD AND TEXT EXTRACTION (Preserving paragraph structure)
# ============================================================================

def sanitize_filename(name):
    """Remove invalid characters from filename"""
    name = re.sub(r'[<>:"/\\|?*]', '_', name)
    return name.strip()

def get_book_name_from_url(url):
    """Extract book name from URL"""
    parsed = urlparse(url)
    filename = unquote(os.path.basename(parsed.path))
    if filename.lower().endswith('.pdf'):
        filename = filename[:-4]
    return sanitize_filename(filename)

def download_pdf(url, temp_path):
    """Download PDF from URL"""
    response = requests.get(url, stream=True, timeout=60)
    response.raise_for_status()
    with open(temp_path, 'wb') as f:
        for chunk in response.iter_content(chunk_size=8192):
            f.write(chunk)
    return temp_path

def extract_text_from_pdf(pdf_path):
    """Extract text from PDF using PyMuPDF"""
    text = ""
    with fitz.open(pdf_path) as doc:
        for page in doc:
            text += page.get_text()
    return text

def is_metadata_line(line):
    """Check if a line is likely metadata (not story content)"""
    line = line.strip()
    if not line:
        return "empty"
    if re.match(r'^\d+$', line):
        return "page_number"
    if re.match(r'^[IVXLCDM]+$', line):
        return "chapter_number"
    if re.match(r'^(Chapitre|CHAPITRE|Chapter|CHAPTER)\s*[IVXLCDM\d]+', line, re.IGNORECASE):
        return "chapter_title"
    if re.match(r'^(Partie|PARTIE|Part|PART|Tome|TOME|Livre|LIVRE)\s*[IVXLCDM\d]+', line, re.IGNORECASE):
        return "part_title"
    return False

def is_header_block(line):
    """Check if line is header/metadata"""
    line = line.strip()
    header_patterns = [
        r'^BeQ$', r'Bibliothèque électronique', r'Collection À tous les vents',
        r'^Volume \d+', r'^version \d+', r'Édition de référence',
        r'^Traduit de', r'^Traduction', r'^Avertissement$', r'^Préface$',
        r'^PRÉFACE$', r'^Introduction$', r'^INTRODUCTION$', r'^Table des matières',
        r'^TABLE DES MATIÈRES', r'©|Copyright', r'ISBN', r'Imprimé en|Printed in',
        r'^Du même auteur', r'Librairie|Éditeur|Éditions', r'^\d{4}$',
        r'^FIN$', r'^fin$', r'^Fin$',
    ]
    for pattern in header_patterns:
        if re.search(pattern, line, re.IGNORECASE):
            return True
    return False

def clean_book_text_preserve_structure(raw_text):
    """
    Clean extracted text but PRESERVE paragraph structure for dialogue extraction.
    Each paragraph is separated by double newline.
    """
    lines = raw_text.split('\n')
    
    # Find where actual content starts
    content_start = 0
    consecutive_long_lines = 0
    for i, line in enumerate(lines):
        stripped = line.strip()
        if len(stripped) > 50 and not is_header_block(stripped):
            consecutive_long_lines += 1
            if consecutive_long_lines >= 3:
                content_start = max(0, i - 3)
                break
        else:
            consecutive_long_lines = 0
    
    # Process lines and build paragraphs (preserve structure!)
    paragraphs = []
    current_paragraph = []
    
    for i in range(content_start, len(lines)):
        line = lines[i]
        stripped = line.strip()
        
        meta_type = is_metadata_line(stripped)
        
        # Skip page numbers and chapter numbers
        if meta_type in ["page_number", "chapter_number"]:
            continue
        
        # Chapter/part titles cause paragraph break but are not included
        if meta_type in ["chapter_title", "part_title"]:
            if current_paragraph:
                paragraphs.append(' '.join(current_paragraph))
                current_paragraph = []
            continue
        
        # Skip header blocks
        if is_header_block(stripped):
            if current_paragraph:
                paragraphs.append(' '.join(current_paragraph))
                current_paragraph = []
            continue
        
        # Skip ALL CAPS lines (titles)
        if stripped.isupper() and len(stripped) > 3:
            if current_paragraph:
                paragraphs.append(' '.join(current_paragraph))
                current_paragraph = []
            continue
        
        # Empty line = paragraph break
        if meta_type == "empty":
            if current_paragraph:
                paragraphs.append(' '.join(current_paragraph))
                current_paragraph = []
            continue
        
        # Regular text line - handle hyphenation
        if current_paragraph and current_paragraph[-1].endswith('-'):
            current_paragraph[-1] = current_paragraph[-1][:-1] + stripped
        else:
            current_paragraph.append(stripped)
    
    if current_paragraph:
        paragraphs.append(' '.join(current_paragraph))
    
    # Join paragraphs with DOUBLE NEWLINE to preserve structure
    result = '\n\n'.join(paragraphs)
    
    # Clean up
    result = re.sub(r' +', ' ', result)
    result = re.sub(r' ([.,;:!?])', r'\1', result)
    result = re.sub(r'([.,;:!?])([A-Za-zÀ-ÿ])', r'\1 \2', result)
    
    return result.strip()

def get_pdf_urls_from_beq(page_url="https://beq.ebooksgratuits.com/vents/"):
    """Scrape all PDF links from the BEQ website"""
    response = requests.get(page_url, timeout=60)
    response.raise_for_status()
    soup = BeautifulSoup(response.content, 'html.parser')
    
    pdf_urls = set()
    for link in soup.find_all('a', href=True):
        href = link['href']
        if href.endswith('.pdf'):
            if href.startswith('http'):
                pdf_urls.add(href)
            else:
                pdf_urls.add(urljoin(page_url, href))
    
    final_urls = []
    for url in sorted(pdf_urls):
        if '/vents/' in url and '/vents-xpdf/' not in url:
            final_urls.append(url)
    
    return final_urls

print("✅ PDF processing functions loaded!")

✅ PDF processing functions loaded!


## Step 2: Dialogue Extraction Functions

In [17]:
# ============================================================================
# DIALOGUE EXTRACTION
# ============================================================================

def extract_dialogues_from_text(text):
    """
    Extract dialogue turns from text using French dialogue markers.
    
    French dialogue conventions:
    - Guillemets « » open/close dialogue sections
    - Dashes (–, —, ―) indicate speaker changes
    - Sometimes dialogue is inline with narrative
    
    Returns a list of dialogue strings.
    """
    dialogues = []
    
    # Split into paragraphs
    paragraphs = text.split('\n\n')
    
    for para in paragraphs:
        para = para.strip()
        if not para:
            continue
        
        # Method 1: Extract content between guillemets
        # Pattern: « dialogue content »
        guillemet_pattern = re.compile(r'«\s*([^»]+)\s*»')
        guillemet_matches = guillemet_pattern.findall(para)
        
        for match in guillemet_matches:
            # Split by dash markers within guillemets (speaker changes)
            parts = re.split(r'\s*[–—―]\s*', match)
            for part in parts:
                cleaned = clean_dialogue_text(part)
                if cleaned and len(cleaned) >= MIN_DIALOGUE_LENGTH:
                    dialogues.append(cleaned)
        
        # Method 2: Lines starting with dash (outside guillemets)
        # This catches dialogue that uses dashes without guillemets
        dash_pattern = re.compile(r'^[–—―-]\s*(.+?)(?=[–—―]|$)', re.MULTILINE)
        
        # Also try splitting by dash at start of sentences
        if not guillemet_matches:
            # Check if paragraph starts with or contains dash-style dialogue
            if any(para.strip().startswith(marker) for marker in DIALOGUE_MARKERS):
                # Split by dialogue markers
                parts = re.split(r'(?:^|\s)[–—―-]\s+', para)
                for part in parts:
                    cleaned = clean_dialogue_text(part)
                    if cleaned and len(cleaned) >= MIN_DIALOGUE_LENGTH:
                        dialogues.append(cleaned)
    
    return dialogues

def clean_dialogue_text(text):
    """
    Clean a dialogue turn by removing speech attribution.
    
    Example:
    "Bonjour, dit-il en souriant." -> "Bonjour"
    "Comment allez-vous ? demanda Marie." -> "Comment allez-vous ?"
    """
    if not text:
        return ""
    
    text = text.strip()
    
    # Remove speech attribution at the end
    text = SPEECH_ATTRIBUTION_PATTERN.sub('', text)
    
    # Also handle mid-sentence attributions like: "Oui, dit-il, je comprends."
    mid_attribution = re.compile(
        r',\s*(dit|répondit|demanda|s\'écria|murmura|ajouta|reprit|continua|'
        r'répliqua|interrompit|chuchota|souffla|fit)'
        r'[-\s]*(il|elle|je|tu|nous|vous|ils|elles|on|'
        r'le\s+\w+|la\s+\w+|l\'\w+|\w+)?'
        r',\s*',
        re.IGNORECASE
    )
    text = mid_attribution.sub(' ', text)
    
    # Clean up whitespace
    text = re.sub(r'\s+', ' ', text)
    text = text.strip()
    
    # Remove leading/trailing punctuation artifacts
    text = re.sub(r'^[,;:\s]+', '', text)
    text = re.sub(r'[,;:\s]+$', '', text)
    
    return text

def extract_dialogues_advanced(text):
    """
    Advanced dialogue extraction with better handling of French text.
    Combines multiple detection strategies.
    """
    all_dialogues = []
    
    # Strategy 1: Guillemet-based extraction (most reliable)
    # Pattern for dialogue within guillemets, handling nested structure
    guillemet_sections = re.findall(r'«([^»]+)»', text)
    
    for section in guillemet_sections:
        # Within a guillemet section, dashes indicate speaker changes
        # Split by dashes that appear after sentence-ending punctuation
        turns = re.split(r'(?<=[.!?])\s*[–—―]\s*', section)
        
        for turn in turns:
            cleaned = clean_dialogue_text(turn)
            if cleaned and len(cleaned) >= MIN_DIALOGUE_LENGTH:
                all_dialogues.append(cleaned)
    
    # Strategy 2: Paragraph-level dash detection
    paragraphs = text.split('\n\n')
    
    for para in paragraphs:
        para = para.strip()
        
        # Skip if we already extracted from guillemets in this paragraph
        if '«' in para and '»' in para:
            continue
        
        # Check for dash-style dialogue (line starts with dash)
        if para and para[0] in DIALOGUE_MARKERS + ['-']:
            # This paragraph is likely a dialogue turn
            cleaned = clean_dialogue_text(para.lstrip('-–—― '))
            if cleaned and len(cleaned) >= MIN_DIALOGUE_LENGTH:
                all_dialogues.append(cleaned)
    
    return all_dialogues

print("✅ Dialogue extraction functions loaded!")

✅ Dialogue extraction functions loaded!


## Step 3: Conversation Building Functions

In [18]:
# ============================================================================
# CONVERSATION BUILDING
# ============================================================================

def build_conversations(dialogues, max_turns=MAX_TURNS_PER_CONVERSATION):
    """
    Build multi-turn conversations from a list of dialogues.
    
    - Pairs consecutive dialogues as user/assistant
    - Creates multi-turn conversations (up to max_turns)
    - Ensures each conversation ends with 'assistant'
    
    Returns list of conversations, each being a list of {role, content} dicts.
    """
    conversations = []
    
    if len(dialogues) < 2:
        return conversations
    
    i = 0
    while i < len(dialogues) - 1:
        conversation = []
        turns_added = 0
        
        while i < len(dialogues) and turns_added < max_turns:
            # Add user turn
            conversation.append({
                "role": "user",
                "content": dialogues[i]
            })
            turns_added += 1
            i += 1
            
            # Add assistant turn if available
            if i < len(dialogues) and turns_added < max_turns:
                conversation.append({
                    "role": "assistant",
                    "content": dialogues[i]
                })
                turns_added += 1
                i += 1
        
        # Ensure conversation ends with assistant
        if conversation and conversation[-1]["role"] == "user":
            # Remove the last user message if there's no assistant response
            conversation.pop()
        
        # Only add if we have at least one exchange (user + assistant)
        if len(conversation) >= 2:
            conversations.append(conversation)
    
    return conversations

def build_conversations_pairs_only(dialogues):
    """
    Build simple 2-turn conversations (user/assistant pairs).
    Each conversation is exactly one exchange.
    """
    conversations = []
    
    for i in range(0, len(dialogues) - 1, 2):
        conversation = [
            {"role": "user", "content": dialogues[i]},
            {"role": "assistant", "content": dialogues[i + 1]}
        ]
        conversations.append(conversation)
    
    return conversations

def build_conversations_sliding_window(dialogues, window_size=4, step=2):
    """
    Build conversations using a sliding window approach.
    Creates overlapping multi-turn conversations for more training data.
    
    Args:
        dialogues: List of dialogue strings
        window_size: Number of turns per conversation (must be even)
        step: How many dialogues to skip between windows
    """
    conversations = []
    
    # Ensure window_size is even (for user/assistant pairs)
    window_size = window_size if window_size % 2 == 0 else window_size - 1
    
    for i in range(0, len(dialogues) - window_size + 1, step):
        window = dialogues[i:i + window_size]
        conversation = []
        
        for j, dialogue in enumerate(window):
            role = "user" if j % 2 == 0 else "assistant"
            conversation.append({"role": role, "content": dialogue})
        
        # Only add if ends with assistant
        if conversation and conversation[-1]["role"] == "assistant":
            conversations.append(conversation)
    
    return conversations



print("✅ Conversation building functions loaded!")

✅ Conversation building functions loaded!


## Step 4: Main Processing Pipeline

In [19]:
# ============================================================================
# MAIN PROCESSING PIPELINE
# ============================================================================

def process_single_book(url, temp_dir="temp_pdfs"):
    """
    Process a single book: download PDF, extract text, find dialogues.
    
    Returns:
        tuple: (book_name, text_with_structure, dialogues)
    """
    os.makedirs(temp_dir, exist_ok=True)
    
    book_name = get_book_name_from_url(url)
    temp_pdf = os.path.join(temp_dir, f"{book_name}.pdf")
    
    try:
        # Download PDF
        download_pdf(url, temp_pdf)
        
        # Extract text
        raw_text = extract_text_from_pdf(temp_pdf)
        
        # Clean text but preserve structure
        cleaned_text = clean_book_text_preserve_structure(raw_text)
        
        # Extract dialogues
        dialogues = extract_dialogues_advanced(cleaned_text)
        
        return book_name, cleaned_text, dialogues
        
    except Exception as e:
        print(f"Error processing {url}: {e}")
        return book_name, "", []
    
    finally:
        # Cleanup
        if os.path.exists(temp_pdf):
            os.remove(temp_pdf)

def process_all_books(urls, conversation_mode="sliding"):
    """
    Process all books and build conversation dataset.
    
    Args:
        urls: List of PDF URLs
        conversation_mode: "pairs" (2-turn), "multi" (variable), "sliding" (overlapping)
    
    Returns:
        List of conversation dicts ready for dataset
    """
    all_conversations = []
    
    for url in tqdm(urls, desc="Processing books"):
        book_name, text, dialogues = process_single_book(url)
        
        if len(dialogues) < 2:
            continue
        
        # Build conversations based on mode
        if conversation_mode == "pairs":
            conversations = build_conversations_pairs_only(dialogues)
        elif conversation_mode == "multi":
            conversations = build_conversations(dialogues)
        elif conversation_mode == "sliding":
            conversations = build_conversations_sliding_window(dialogues, window_size=6, step=2)
        else:
            conversations = build_conversations_pairs_only(dialogues)
        
        all_conversations.extend(conversations)
        
        print(f"  {book_name}: {len(dialogues)} dialogues → {len(conversations)} conversations")
    
    return all_conversations

print("✅ Processing pipeline loaded!")

✅ Processing pipeline loaded!


## Step 5: Get PDF URLs and Test on Sample

In [20]:
# Fetch all PDF URLs from BEQ website
print("Fetching PDF links from https://beq.ebooksgratuits.com/vents/ ...")
pdf_urls = get_pdf_urls_from_beq()
print(f"Found {len(pdf_urls)} PDF files!\n")

# Show first 10 as preview
print("First 10 PDFs:")
for i, url in enumerate(pdf_urls[:10], 1):
    print(f"  {i}. {url.split('/')[-1]}")

Fetching PDF links from https://beq.ebooksgratuits.com/vents/ ...
Found 725 PDF files!

First 10 PDFs:
  1. About-Germaine.pdf
  2. About-montagnes.pdf
  3. About_Le_nez_dun_notaire.pdf
  4. About_Lhomme_a_loreille_cassee.pdf
  5. Abrantes-Marina.pdf
  6. Abrantes-Mathilde.pdf
  7. Achard-Madame.pdf
  8. Achard-dort.pdf
  9. Achard-soldat.pdf
  10. Adam-mesaventure.pdf
Found 725 PDF files!

First 10 PDFs:
  1. About-Germaine.pdf
  2. About-montagnes.pdf
  3. About_Le_nez_dun_notaire.pdf
  4. About_Lhomme_a_loreille_cassee.pdf
  5. Abrantes-Marina.pdf
  6. Abrantes-Mathilde.pdf
  7. Achard-Madame.pdf
  8. Achard-dort.pdf
  9. Achard-soldat.pdf
  10. Adam-mesaventure.pdf


In [21]:
# ============================================================================
# TEST: Process a single book to verify dialogue extraction works
# ============================================================================

# Pick a book likely to have good dialogues (Balzac, Dumas, etc.)
test_url = pdf_urls[0]  # First available book
print(f"Testing with: {test_url.split('/')[-1]}\n")

book_name, text, dialogues = process_single_book(test_url)

print(f"Book: {book_name}")
print(f"Text length: {len(text):,} characters")
print(f"Dialogues found: {len(dialogues)}")

if dialogues:
    print(f"\n{'='*60}")
    print("Sample dialogues extracted:")
    print('='*60)
    for i, d in enumerate(dialogues[:10], 1):
        print(f"\n[{i}] {d[:200]}{'...' if len(d) > 200 else ''}")

Testing with: About-Germaine.pdf

Book: About-Germaine
Text length: 390,389 characters
Dialogues found: 674

Sample dialogues extracted:

[1] Avec ça et ce que j’ai de côté, disait le maître d’hôtel, j’arrondirai ma rente viagère. On a du pain sur la planche, Dieu merci! et l’on ne se laissera manquer de rien sur ses vieux jours.

[2] Parbleu! reprit le valet de chambre, vous êtes garçon; vous n’avez que vous à penser. Mais, moi, j’ai de la famille. Aussi, je donnerai mon argent à ce petit jeune homme qui va à la Bourse. Il me trip...

[3] C’est une idée, ça, monsieur Ferdinand, repartit le marmiton. Portez-lui donc mes quarante francs, quand vous irez.

[4] Est-il jeune! Qu’est-ce qu’on peut faire à la Bourse avec quarante francs?

[5] Allons, dit le jeune homme en étouffant un soupir, je les mettrai à la caisse d’épargne!

[6] Ma caisse d’épargne, à moi, la voici. C’est là que j’ai toujours placé mes fonds, et je m’en suis bien trouvé. Pas vrai, père Altroff?

[7] Allais, marchais! c

In [22]:
# ============================================================================
# TEST: Build sample conversations
# ============================================================================

if len(dialogues) >= 2:
    # Test different conversation modes
    print("Testing conversation building modes:\n")
    
    # Pairs only
    conv_pairs = build_conversations_pairs_only(dialogues)
    print(f"Pairs mode: {len(conv_pairs)} conversations")
    
    # Multi-turn
    conv_multi = build_conversations(dialogues, max_turns=6)
    print(f"Multi-turn mode: {len(conv_multi)} conversations")
    
    # Sliding window
    conv_sliding = build_conversations_sliding_window(dialogues, window_size=4, step=2)
    print(f"Sliding window mode: {len(conv_sliding)} conversations")
    
    # Show a sample conversation
    if conv_sliding:
        print(f"\n{'='*60}")
        print("Sample conversation:")
        print('='*60)
        print(json.dumps(conv_sliding[0], indent=2, ensure_ascii=False))

Testing conversation building modes:

Pairs mode: 337 conversations
Multi-turn mode: 113 conversations
Sliding window mode: 336 conversations

Sample conversation:
[
  {
    "role": "user",
    "content": "Avec ça et ce que j’ai de côté, disait le maître d’hôtel, j’arrondirai ma rente viagère. On a du pain sur la planche, Dieu merci! et l’on ne se laissera manquer de rien sur ses vieux jours."
  },
  {
    "role": "assistant",
    "content": "Parbleu! reprit le valet de chambre, vous êtes garçon; vous n’avez que vous à penser. Mais, moi, j’ai de la famille. Aussi, je donnerai mon argent à ce petit jeune homme qui va à la Bourse. Il me tripotera quelque chose."
  },
  {
    "role": "user",
    "content": "C’est une idée, ça, monsieur Ferdinand, repartit le marmiton. Portez-lui donc mes quarante francs, quand vous irez."
  },
  {
    "role": "assistant",
    "content": "Est-il jeune! Qu’est-ce qu’on peut faire à la Bourse avec quarante francs?"
  }
]


## Step 6: Process All Books (Full Run)

In [23]:
# ============================================================================
# FULL PROCESSING: Process all books
# ============================================================================
# WARNING: This will take a long time! Consider starting with a smaller subset.

# Configuration
URLS_TO_PROCESS = pdf_urls[:700]  # Adjust this number as needed
CONVERSATION_MODE = "sliding"     # "pairs", "multi", or "sliding"

print(f"Processing {len(URLS_TO_PROCESS)} books...")
print(f"Mode: {CONVERSATION_MODE}")
print()

all_conversations = process_all_books(
    URLS_TO_PROCESS,
    conversation_mode=CONVERSATION_MODE
)

print(f"\n{'='*60}")
print(f"TOTAL CONVERSATIONS: {len(all_conversations)}")
print('='*60)

Processing 700 books...
Mode: sliding



Processing books:   0%|          | 1/700 [00:01<12:05,  1.04s/it]

  About-Germaine: 674 dialogues → 335 conversations


Processing books:   0%|          | 2/700 [00:02<11:33,  1.01it/s]

  About-montagnes: 126 dialogues → 61 conversations


...

  loti-matelot: 46 dialogues → 21 conversations


Processing books: 100%|█████████▉| 699/700 [09:40<00:00,  1.35it/s]

  merimee-1: 850 dialogues → 423 conversations


Processing books: 100%|██████████| 700/700 [09:41<00:00,  1.20it/s]

  merimee-2: 155 dialogues → 75 conversations

TOTAL CONVERSATIONS: 77583


## Step 7: Create and Upload Dataset to HuggingFace

In [24]:
# Login to Hugging Face
login()

In [25]:
# ============================================================================
# CREATE DATASET
# ============================================================================

def create_conversation_dataset(conversations, dataset_name, username):
    """
    Create and upload a conversation dataset to HuggingFace Hub.
    
    The dataset will have a 'conversations' column compatible with:
    - ShareGPT format
    - ChatML format
    - Most finetuning frameworks (axolotl, unsloth, etc.)
    """
    
    # Convert conversations to the format expected by most finetuning tools
    # Each row has a 'conversations' field which is a list of message dicts
    data = {
        "conversations": [json.dumps(conv, ensure_ascii=False) for conv in conversations]
    }
    
    dataset = Dataset.from_dict(data)
    
    print(f"Dataset created with {len(dataset)} conversations")
    print(f"Sample row:\n{dataset[0]}\n")
    
    # Push to Hub
    repo_id = f"{username}/{dataset_name}"
    print(f"Uploading to HuggingFace Hub as '{repo_id}'...")
    
    dataset.push_to_hub(repo_id, private=False)
    
    print(f"\n✅ Dataset uploaded successfully!")
    print(f"View it at: https://huggingface.co/datasets/{repo_id}")
    
    return dataset

# Create and upload the dataset
dataset = create_conversation_dataset(
    all_conversations,
    dataset_name="french-classic-conversations",
    username="Volko76"  # Your HF username
)

Dataset created with 77583 conversations
Sample row:
{'conversations': '[{"role": "user", "content": "Avec ça et ce que j’ai de côté, disait le maître d’hôtel, j’arrondirai ma rente viagère. On a du pain sur la planche, Dieu merci! et l’on ne se laissera manquer de rien sur ses vieux jours."}, {"role": "assistant", "content": "Parbleu! reprit le valet de chambre, vous êtes garçon; vous n’avez que vous à penser. Mais, moi, j’ai de la famille. Aussi, je donnerai mon argent à ce petit jeune homme qui va à la Bourse. Il me tripotera quelque chose."}, {"role": "user", "content": "C’est une idée, ça, monsieur Ferdinand, repartit le marmiton. Portez-lui donc mes quarante francs, quand vous irez."}, {"role": "assistant", "content": "Est-il jeune! Qu’est-ce qu’on peut faire à la Bourse avec quarante francs?"}, {"role": "user", "content": "Allons, dit le jeune homme en étouffant un soupir, je les mettrai à la caisse d’épargne!"}, {"role": "assistant", "content": "Ma caisse d’épargne, à moi, la v

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ? shards/s]

Creating parquet from Arrow format:   0%|          | 0/78 [00:00<?, ?ba/s]

Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

                              :   0%|          | 93.0kB / 33.3MB            

README.md:   0%|          | 0.00/416 [00:00<?, ?B/s]


✅ Dataset uploaded successfully!
View it at: https://huggingface.co/datasets/Volko76/french-classic-conversations


## Step 8: Dataset Statistics and Validation

In [26]:
# ============================================================================
# DATASET STATISTICS
# ============================================================================

def analyze_dataset(conversations):
    """Compute statistics about the conversation dataset."""
    
    total_convos = len(conversations)
    
    # Count turns
    turn_counts = [len(conv) for conv in conversations]
    avg_turns = sum(turn_counts) / total_convos if total_convos > 0 else 0
    
    # Count characters
    total_chars = 0
    user_chars = 0
    assistant_chars = 0
    
    for conv in conversations:
        for msg in conv:
            chars = len(msg['content'])
            total_chars += chars
            if msg['role'] == 'user':
                user_chars += chars
            elif msg['role'] == 'assistant':
                assistant_chars += chars
    
    print("📊 Dataset Statistics")
    print("=" * 40)
    print(f"Total conversations: {total_convos:,}")
    print(f"Average turns per conversation: {avg_turns:.1f}")
    print(f"Min turns: {min(turn_counts) if turn_counts else 0}")
    print(f"Max turns: {max(turn_counts) if turn_counts else 0}")
    print(f"\nTotal characters: {total_chars:,}")
    print(f"User characters: {user_chars:,}")
    print(f"Assistant characters: {assistant_chars:,}")
    print(f"\nAvg chars per conversation: {total_chars // total_convos if total_convos else 0:,}")

# Analyze the dataset
analyze_dataset(all_conversations)

# Show a few random samples
import random
print(f"\n{'='*60}")
print("Random conversation samples:")
print('='*60)

for i, conv in enumerate(random.sample(all_conversations, min(3, len(all_conversations))), 1):
    print(f"\n--- Sample {i} ---")
    print(json.dumps(conv, indent=2, ensure_ascii=False)[:1000])
    print("...")

📊 Dataset Statistics
Total conversations: 77,583
Average turns per conversation: 6.0
Min turns: 6
Max turns: 6

Total characters: 102,931,512
User characters: 51,646,277
Assistant characters: 51,285,235

Avg chars per conversation: 1,326

Random conversation samples:

--- Sample 1 ---
[
  {
    "role": "user",
    "content": "Ça, c’est sûr. Que le bon Dieu nous garde le colonel, car, s’il n’était plus là, Mlle Trépiez nous reviendrait peut-être."
  },
  {
    "role": "assistant",
    "content": "Elle serait capable d’essayer! En attendant, elle ne fait rien de bon à Paris. On dit que ses cancans brouillent de plus en plus M. Robert avec ce camarade qu’il n’aimait pas; tu sais?"
  },
  {
    "role": "user",
    "content": "Ah! celui dont il parlait toujours en montrant le poing, Horace Croquart? Il paraît que c’est un mauvais diable, lui; tandis que le nôtre, c’est un bon diable."
  },
  {
    "role": "assistant",
    "content": "Déjà pas si bon!"
  },
  {
    "role": "user",
    "conte

## Optional: Export to Different Formats

The cell below allows you to export the dataset in different formats commonly used for finetuning.

In [27]:
# ============================================================================
# EXPORT TO DIFFERENT FORMATS AND UPLOAD TO HF REPO
# ============================================================================

from huggingface_hub import HfApi
import tempfile

def export_and_upload_formats(conversations, repo_id="Volko76/french-classic-conversations"):
    """
    Export conversations to different formats and upload to HuggingFace repo.
    """
    api = HfApi()
    
    # Create temporary files and upload each format
    with tempfile.TemporaryDirectory() as tmpdir:
        
        # 1. ShareGPT format
        sharegpt_path = os.path.join(tmpdir, "sharegpt_format.json")
        sharegpt_data = []
        for conv in conversations:
            sharegpt_conv = {
                "conversations": [
                    {"from": "human" if msg["role"] == "user" else "gpt", 
                     "value": msg["content"]}
                    for msg in conv
                ]
            }
            sharegpt_data.append(sharegpt_conv)
        
        with open(sharegpt_path, 'w', encoding='utf-8') as f:
            json.dump(sharegpt_data, f, ensure_ascii=False, indent=2)
        
        api.upload_file(
            path_or_fileobj=sharegpt_path,
            path_in_repo="sharegpt_format.json",
            repo_id=repo_id,
            repo_type="dataset"
        )
        print(f"✅ Uploaded ShareGPT format")
        
        # 2. ChatML format (JSONL)
        chatml_path = os.path.join(tmpdir, "chatml_format.jsonl")
        with open(chatml_path, 'w', encoding='utf-8') as f:
            for conv in conversations:
                chatml_text = ""
                for msg in conv:
                    role = msg["role"]
                    content = msg["content"]
                    chatml_text += f"<|im_start|>{role}\n{content}<|im_end|>\n"
                f.write(json.dumps({"text": chatml_text}, ensure_ascii=False) + "\n")
        
        api.upload_file(
            path_or_fileobj=chatml_path,
            path_in_repo="chatml_format.jsonl",
            repo_id=repo_id,
            repo_type="dataset"
        )
        print(f"✅ Uploaded ChatML format")
        
        # 3. Alpaca format
        alpaca_path = os.path.join(tmpdir, "alpaca_format.json")
        alpaca_data = []
        for conv in conversations:
            user_msg = None
            assistant_msg = None
            for msg in conv:
                if msg["role"] == "user" and user_msg is None:
                    user_msg = msg["content"]
                elif msg["role"] == "assistant" and assistant_msg is None:
                    assistant_msg = msg["content"]
            if user_msg and assistant_msg:
                alpaca_data.append({
                    "instruction": "",
                    "input": user_msg,
                    "output": assistant_msg
                })
        
        with open(alpaca_path, 'w', encoding='utf-8') as f:
            json.dump(alpaca_data, f, ensure_ascii=False, indent=2)
        
        api.upload_file(
            path_or_fileobj=alpaca_path,
            path_in_repo="alpaca_format.json",
            repo_id=repo_id,
            repo_type="dataset"
        )
        print(f"✅ Uploaded Alpaca format")
    
    print(f"\n🎉 All formats uploaded to https://huggingface.co/datasets/{repo_id}")

# Export and upload all formats to the HF repo
export_and_upload_formats(all_conversations, repo_id="Volko76/french-classic-conversations")

Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

  ...yp6t/sharegpt_format.json:  16%|#6        | 22.7MB /  139MB            

✅ Uploaded ShareGPT format


Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

...

✅ Uploaded ChatML format


Processing Files (0 / 0)      : |          |  0.00B /  0.00B            

New Data Upload               : |          |  0.00B /  0.00B            

  ...bzyp6t/alpaca_format.json:  16%|#6        | 6.50MB / 40.6MB            

✅ Uploaded Alpaca format

🎉 All formats uploaded to https://huggingface.co/datasets/Volko76/french-classic-conversations
